# Introduction to the xgbsurv package

This notebook introduces `xgbsurv` using a specific dataset. It structured by the following steps:

- Load data
- Load model
- Fit model
- Predict and evaluate model

The syntax conveniently follows that of sklearn.

In [1]:
from xgbsurv.datasets import load_metabric
from xgbsurv import XGBSurv
from sklearn.model_selection import train_test_split
import numpy as np
%load_ext autoreload
%autoreload 2


## Load Data

In [2]:
data, target = load_metabric(path="/Users/JUSC/Documents/xgbsurv/xgbsurv/datasets/data/", as_frame=False)
target_sign = np.sign(target)
X_train, X_test, y_train, y_test = train_test_split(data, target, stratify=target_sign)

## Load Model

In [7]:
model = XGBSurv(n_estimators=25, objective="breslow_objective",
                                             eval_metric="breslow_loss",
                                             learning_rate=0.3,
                                             random_state=7, 
                                             disable_default_eval_metric=True)

The options of loss and objective functions can be obtained like below:

In [8]:
print(model.get_loss_functions().keys())
print(model.get_objective_functions().keys())

dict_keys(['breslow_loss', 'efron_loss', 'cind_loss', 'deephit_loss', 'aft_loss'])
dict_keys(['breslow_objective', 'efron_objective', 'cind_objective', 'deephit_objective', 'aft_objective'])


## Fit Model

In [9]:
eval_set = [(X_train, y_train)]

In [10]:
model.fit(X_train, y_train, eval_set=eval_set)

[0]	validation_0-breslow_likelihood:6.20744
[1]	validation_0-breslow_likelihood:6.12331
[2]	validation_0-breslow_likelihood:6.06036
[3]	validation_0-breslow_likelihood:6.00969
[4]	validation_0-breslow_likelihood:5.97407
[5]	validation_0-breslow_likelihood:5.94184
[6]	validation_0-breslow_likelihood:5.88654
[7]	validation_0-breslow_likelihood:5.85201
[8]	validation_0-breslow_likelihood:5.81938
[9]	validation_0-breslow_likelihood:5.79397
[10]	validation_0-breslow_likelihood:5.75736
[11]	validation_0-breslow_likelihood:5.73451
[12]	validation_0-breslow_likelihood:5.72002
[13]	validation_0-breslow_likelihood:5.69969
[14]	validation_0-breslow_likelihood:5.69166
[15]	validation_0-breslow_likelihood:5.67384
[16]	validation_0-breslow_likelihood:5.65022
[17]	validation_0-breslow_likelihood:5.64190
[18]	validation_0-breslow_likelihood:5.62294
[19]	validation_0-breslow_likelihood:5.60722
[20]	validation_0-breslow_likelihood:5.59743
[21]	validation_0-breslow_likelihood:5.58604
[22]	validation_0-br

XGBSurv(base_score=None, booster=None, callbacks=None, colsample_bylevel=None,
        colsample_bynode=None, colsample_bytree=None,
        disable_default_eval_metric=True, early_stopping_rounds=None,
        enable_categorical=False,
        eval_metric=CPUDispatcher(<function breslow_likelihood at 0x7fdb599a1240>),
        feature_types=None, gamma=None, gpu_id=None, grow_policy=None,
        importance_type=None, interaction_constraints=None, learning_rate=0.3,
        max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
        max_delta_step=None, max_depth=None, max_leaves=None,
        min_child_weight=None, missing=nan, monotone_constraints=None,
        n_estimators=25, n_jobs=None, num_parallel_tree=None,
        objective=CPUDispatcher(<function breslow_objective at 0x7fdb599a1750>), ...)

The model can be saved like below. Note that objective and eval_metric are not saved.

In [7]:
model.save_model("introduction_model.json")

/Users/JUSC/miniconda3/envs/xgbsurv/lib/python3.10/site-packages/xgboost/sklearn.py:761: UserWarning: objective is not saved in Scikit-Learn meta.
  warnings.warn(
/Users/JUSC/miniconda3/envs/xgbsurv/lib/python3.10/site-packages/xgboost/sklearn.py:761: UserWarning: eval_metric is not saved in Scikit-Learn meta.
  warnings.warn(
/Users/JUSC/miniconda3/envs/xgbsurv/lib/python3.10/site-packages/xgboost/sklearn.py:761: UserWarning: y is not saved in Scikit-Learn meta.
  warnings.warn(


## Predict

In [21]:
preds_train = model.predict(X_train, output_margin=True)
preds_test = model.predict(X_test, output_margin=True)

### Predict Cumulative Hazard

In [20]:
df_cum_hazards = model.predict_cumulative_hazard_function(data, dataframe=True)
df_cum_hazards.head(5)

(1309,) (1309,)


time  patient_0  patient_1  patient_2  patient_3  patient_4  patient_5  \
0  0.766667   0.000000   0.000000   0.000000   0.000000   0.000000    0.00000   
1  1.266667   0.000000   0.000000   0.000000   0.000000   0.000000    0.00000   
2  1.433333   0.000000   0.000000   0.000000   0.000000   0.000000    0.00000   
3  2.000000   0.000000   0.000000   0.000000   0.000000   0.000000    0.00000   
4  2.300000   0.001246   0.000285   0.000495   0.000219   0.000427    0.00046   

   patient_6  patient_7  patient_8  ...  patient_1893  patient_1894  \
0   0.000000   0.000000   0.000000  ...      0.000000      0.000000   
1   0.000000   0.000000   0.000000  ...      0.000000      0.000000   
2   0.000000   0.000000   0.000000  ...      0.000000      0.000000   
3   0.000000   0.000000   0.000000  ...      0.000000      0.000000   
4   0.000211   0.000674   0.000607  ...      0.000736      0.000438   

   patient_1895  patient_1896  patient_1897  patient_1898  patient_1899  \
0      0.000000      0.000000      0.000000      0.000000      0.000000   
1      0.000000      0.000000      0.000000      0.000000      0.000000   
2      0.000000      0.000000      0.000000      0.000000      0.000000   
3      0.000000      0.000000      0.000000      0.000000      0.000000   
4      0.000237      0.000414      0.000335      0.000398      0.000727   

   patient_1900  patient_1901  patient_1902  
0      0.000000      0.000000      0.000000  
1      0.000000      0.000000      0.000000  
2      0.000000      0.000000      0.000000  
3      0.000000      0.000000      0.000000  
4      0.000494      0.001021      0.001034  

[5 rows x 1904 columns]

In [ ]:
df_cum_hazards.to_csv('test.csv')

In [ ]:
np.savetxt("preds.csv", preds, delimiter=",")

In [ ]:
len(np.unique(np.absolute(target)))

1685

### Predict Survival Function

In [ ]:
df_survival = model.predict_survival_function(data, dataframe=True)
df_survival

time      patient_0      patient_1      patient_2      patient_3  \
0       0.100000   9.994107e-01   9.995238e-01   9.994486e-01   9.994167e-01   
1       0.766667   9.982309e-01   9.985704e-01   9.983447e-01   9.982488e-01   
2       1.233333   9.964618e-01   9.971403e-01   9.966892e-01   9.964975e-01   
3       1.266667   9.941055e-01   9.952349e-01   9.944840e-01   9.941651e-01   
4       1.433333   9.911657e-01   9.928563e-01   9.917321e-01   9.912548e-01   
...          ...            ...            ...            ...            ...   
1680  335.600000  4.656672e-217  1.646696e-175  3.954090e-203  7.237864e-215   
1681  335.733340  4.656672e-217  1.646696e-175  3.954090e-203  7.237864e-215   
1682  337.033330  4.656672e-217  1.646696e-175  3.954090e-203  7.237864e-215   
1683  351.000000  4.656672e-217  1.646696e-175  3.954090e-203  7.237864e-215   
1684  355.200000  4.656672e-217  1.646696e-175  3.954090e-203  7.237864e-215   

          patient_4      patient_5      patient_6      patient_7  \
0      9.995634e-01   9.993687e-01   9.995238e-01   9.993648e-01   
1      9.986892e-01   9.981049e-01   9.985704e-01   9.980931e-01   
2      9.973777e-01   9.962100e-01   9.971403e-01   9.961864e-01   
3      9.956301e-01   9.936866e-01   9.952349e-01   9.936474e-01   
4      9.934482e-01   9.905388e-01   9.928563e-01   9.904802e-01   
...             ...            ...            ...            ...   
1680  5.566516e-161  1.755569e-232  1.646696e-175  6.337285e-234   
1681  5.566516e-161  1.755569e-232  1.646696e-175  6.337285e-234   
1682  5.566516e-161  1.755569e-232  1.646696e-175  6.337285e-234   
1683  5.566516e-161  1.755569e-232  1.646696e-175  6.337285e-234   
1684  5.566516e-161  1.755569e-232  1.646696e-175  6.337285e-234   

          patient_8  ...   patient_1893   patient_1894   patient_1895  \
0      9.995191e-01  ...   9.995238e-01   9.995238e-01   9.995093e-01   
1      9.985563e-01  ...   9.985704e-01   9.985704e-01   9.985267e-01   
2      9.971122e-01  ...   9.971403e-01   9.971403e-01   9.970530e-01   
3      9.951880e-01  ...   9.952349e-01   9.952349e-01   9.950896e-01   
4      9.927861e-01  ...   9.928563e-01   9.928563e-01   9.926387e-01   
...             ...  ...            ...            ...            ...   
1680  3.116488e-177  ...  1.646696e-175  1.646696e-175  7.458802e-181   
1681  3.116488e-177  ...  1.646696e-175  1.646696e-175  7.458802e-181   
1682  3.116488e-177  ...  1.646696e-175  1.646696e-175  7.458802e-181   
1683  3.116488e-177  ...  1.646696e-175  1.646696e-175  7.458802e-181   
1684  3.116488e-177  ...  1.646696e-175  1.646696e-175  7.458802e-181   

       patient_1896   patient_1897   patient_1898   patient_1899  \
0      9.994119e-01   9.995317e-01   9.995317e-01   9.995076e-01   
1      9.982345e-01   9.985940e-01   9.985940e-01   9.985216e-01   
2      9.964690e-01   9.971875e-01   9.971875e-01   9.970428e-01   
3      9.941176e-01   9.953134e-01   9.953134e-01   9.950726e-01   
4      9.911838e-01   9.929738e-01   9.929738e-01   9.926133e-01   
...             ...            ...            ...            ...   
1680  1.300179e-216  1.265915e-172  1.265915e-172  1.774117e-181   
1681  1.300179e-216  1.265915e-172  1.265915e-172  1.774117e-181   
1682  1.300179e-216  1.265915e-172  1.265915e-172  1.774117e-181   
1683  1.300179e-216  1.265915e-172  1.265915e-172  1.774117e-181   
1684  1.300179e-216  1.265915e-172  1.265915e-172  1.774117e-181   

       patient_1900   patient_1901   patient_1902  
0      9.995238e-01   9.995238e-01   9.995680e-01  
1      9.985704e-01   9.985704e-01   9.987028e-01  
2      9.971403e-01   9.971403e-01   9.974050e-01  
3      9.952349e-01   9.952349e-01   9.956755e-01  
4      9.928563e-01   9.928563e-01   9.935161e-01  
...             ...            ...            ...  
1680  1.646696e-175  1.646696e-175  2.578949e-159  
1681  1.646696e-175  1.646696e-175  2.578949e-159  
1682  1.646696e-175  1.646696e-175  2.578949e-159  
1683  1.646696e-175 

### Visualize Predictions

In [ ]:
import sys
!conda install --yes --prefix {sys.prefix} -c plotly plotly_express
!conda install --yes --prefix {sys.prefix} -c ipykernel
import plotly_express as px

Solving environment: done

## Package Plan ##

  environment location: /Users/JUSC/miniconda3/envs/xgbsurv

  added / updated specs:
    - plotly_express


The following NEW packages will be INSTALLED:

  patsy              pkgs/main/osx-64::patsy-0.5.3-py310hecd8cb5_0 
  plotly             plotly/noarch::plotly-5.13.1-py_0 
  plotly_express     plotly/noarch::plotly_express-0.4.1-py_0 
  statsmodels        pkgs/main/osx-64::statsmodels-0.13.5-py310h7b7cdfe_1 
  tenacity           pkgs/main/osx-64::tenacity-8.0.1-py310hecd8cb5_1 




Preparing transaction: done
Verifying transaction: done
Executing transaction: done

CondaValueError: too few arguments, must supply command line package specs or --file



In [ ]:
# cumhazard
px.line(df_cum_hazards, x= 'time',y = df_cum_hazards.columns[1:4],range_y=[0,1], title='Cumulative Hazard over Time')


In [ ]:
# survival function
px.line(df_survival, x= 'time',y = df_cum_hazards.columns[1:4],range_y=[0,1], title='Survival Function over Time')



In [ ]:
!conda remove --yes --prefix {sys.prefix} -c plotly plotly_express
!conda remove --yes --prefix {sys.prefix} -c nbformat

Solving environment: done

## Package Plan ##

  environment location: /Users/JUSC/miniconda3/envs/xgbsurv

  removed specs:
    - plotly_express


The following packages will be REMOVED:

  patsy-0.5.3-py310hecd8cb5_0
  plotly-5.13.1-py_0
  plotly_express-0.4.1-py_0
  statsmodels-0.13.5-py310h7b7cdfe_1
  tenacity-8.0.1-py310hecd8cb5_1


Preparing transaction: done
Verifying transaction: done
Executing transaction: done

CondaValueError: no package names supplied,
       try "conda remove -h" for more details



## Evaluate

In [23]:
#from sksurv.metrics import concordance_index_censored
from xgbsurv.evaluation import cindex_censored, ibs

In [25]:
# train
cindex_censored(y_train, preds_train)

0.7102001879632835

In [26]:
# test
cindex_censored(y_test, preds_test)

0.5942479193362585

In [ ]:
times = np.arange(356)
ibs(target, target, preds, times)

TypeError: 'numpy.float32' object is not callable

In [ ]:
import numpy as np
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split

# create dummy data with 20 samples and 14 features
X = np.random.rand(20, 14)

# create dummy target variable with shape (20,)
y = np.random.randint(low=0, high=2, size=20)

# create dummy prediction array with shape (20, 14)
y_pred = np.zeros((20, 14))

# split data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# set up XGBoost classifier with default parameters
xgb = XGBClassifier(classes=['class_1', 'class_2'])

# fit model on training data
xgb.fit(X_train, y_train)

# make predictions on test data
y_pred = xgb.predict(X_train)

# evaluate accuracy of predictions
# accuracy = np.mean(y_pred == y_test)
# print(f"Accuracy: {accuracy}")

[18:37:15] WARNING: /var/folders/sy/f16zz6x50xz3113nwtb9bvq00000gp/T/abs_b2k4a2hea3/croot/xgboost-split_1675457783214/work/src/learner.cc:767: 
Parameters: { "classes" } are not used.



In [ ]:
y.shape

(20,)

In [ ]:
y_pred.shape

(16,)

In [ ]:
X_train.shape

(16, 14)

In [ ]:
df_survival

time  patient_0  patient_1  patient_2  patient_3  patient_4  \
0       0.100000   0.999411   0.999524   0.999449   0.999417   0.999563   
1       0.766667   0.999411   0.999524   0.999449   0.999417   0.999563   
2       1.233333   0.999411   0.999524   0.999449   0.999417   0.999563   
3       1.266667   0.999411   0.999524   0.999449   0.999417   0.999563   
4       1.433333   0.999411   0.999524   0.999449   0.999417   0.999563   
...          ...        ...        ...        ...        ...        ...   
1680  335.600000   0.071382   0.118476   0.084590   0.073326   0.141452   
1681  335.733340   0.052148   0.091928   0.063057   0.053739   0.112094   
1682  337.033330   0.052148   0.091928   0.063057   0.053739   0.112094   
1683  351.000000   0.027257   0.054421   0.034363   0.028275   0.069314   
1684  355.200000   0.006970   0.018080   0.009593   0.007331   0.025236   

      patient_5  patient_6  patient_7  patient_8  ...  patient_1893  \
0      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
1      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
2      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
3      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
4      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
...         ...        ...        ...        ...  ...           ...   
1680   0.059152   0.118476   0.058105   0.116011  ...      0.118476   
1681   0.042258   0.091928   0.041422   0.089790  ...      0.091928   
1682   0.042258   0.091928   0.041422   0.089790  ...      0.091928   
1683   0.021090   0.054421   0.020583   0.052882  ...      0.054421   
1684   0.004894   0.018080   0.004732   0.017379  ...      0.018080   

      patient_1894  patient_1895  patient_1896  patient_1897  patient_1898  \
0         0.999524      0.999509      0.999412      0.999532      0.999532   
1         0.999524      0.999509      0.999412      0.999532      0.999532   
2         0.999524      0.999509      0.999412      0.999532      0.999532   
3         0.999524      0.999509      0.999412      0.999532      0.999532   
4         0.999524      0.999509      0.999412      0.999532      0.999532   
...            ...           ...           ...           ...           ...   
1680      0.118476      0.110997      0.071763      0.122733      0.122733   
1681      0.091928      0.085460      0.052459      0.095632      0.095632   
1682      0.091928      0.085460      0.052459      0.095632      0.095632   
1683      0.054421      0.049788      0.027456      0.057107      0.057107   
1684      0.018080      0.015993      0.007040      0.019322      0.019322   

      patient_1899  patient_1900  patient_1901  patient_1902  
0         0.999508      0.999524      0.999524      0.999568  
1         0.999508      0.999524      0.999524      0.999568  
2         0.999508      0.999524      0.999524      0.999568  
3         0.999508      0.999524      0.999524      0.999568  
4         0.999508      0.999524      0.999524      0.999568  
...            ...           ...           ...           ...  
1680      0.110159      0.118476      0.118476      0.144324  
1681      0.084738      0.091928      0.091928      0.114644  
1682      0.084738      0.091928      0.091928      0.114644  
1683      0.049275      0.054421      0.054421      0.071242  
1684      0.015766      0.018080      0.018080      0.026208  

[1685 rows x 1904 columns]

In [ ]:
from sksurv.datasets import load_gbsg2
X, y = load_gbsg2()

In [ ]:
df_survival.pivot(columns = 'time', )

patient_0                                                         \
time 0.100000   0.766667   1.233333   1.266667   1.433333   1.766667     
0      0.999411        NaN        NaN        NaN        NaN        NaN   
1           NaN   0.999411        NaN        NaN        NaN        NaN   
2           NaN        NaN   0.999411        NaN        NaN        NaN   
3           NaN        NaN        NaN   0.999411        NaN        NaN   
4           NaN        NaN        NaN        NaN   0.999411        NaN   
...         ...        ...        ...        ...        ...        ...   
1680        NaN        NaN        NaN        NaN        NaN        NaN   
1681        NaN        NaN        NaN        NaN        NaN        NaN   
1682        NaN        NaN        NaN        NaN        NaN        NaN   
1683        NaN        NaN        NaN        NaN        NaN        NaN   
1684        NaN        NaN        NaN        NaN        NaN        NaN   

                                                  ... patient_1902             \
time 2.000000   2.300000   2.400000   2.500000    ...   307.633330 307.933320   
0           NaN        NaN        NaN        NaN  ...          NaN        NaN   
1           NaN        NaN        NaN        NaN  ...          NaN        NaN   
2           NaN        NaN        NaN        NaN  ...          NaN        NaN   
3           NaN        NaN        NaN        NaN  ...          NaN        NaN   
4           NaN        NaN        NaN        NaN  ...          NaN        NaN   
...         ...        ...        ...        ...  ...          ...        ...   
1680        NaN        NaN        NaN        NaN  ...          NaN        NaN   
1681        NaN        NaN        NaN        NaN  ...          NaN        NaN   
1682        NaN        NaN        NaN        NaN  ...          NaN        NaN   
1683        NaN        NaN        NaN        NaN  ...          NaN        NaN   
1684        NaN        NaN        NaN        NaN  ...          NaN        NaN   

                                                                        \
time 318.200000 322.833340 330.366670 335.600000 335.733340 337.033330   
0           NaN        NaN        NaN        NaN        NaN        NaN   
1           NaN        NaN        NaN        NaN        NaN        NaN   
2           NaN        NaN        NaN        NaN        NaN        NaN   
3           NaN        NaN        NaN        NaN        NaN        NaN   
4           NaN        NaN        NaN        NaN        NaN        NaN   
...         ...        ...        ...        ...        ...        ...   
1680        NaN        NaN        NaN   0.144324        NaN        NaN   
1681        NaN        NaN        NaN        NaN   0.114644        NaN   
1682        NaN        NaN        NaN        NaN        NaN   0.114644   
1683        NaN        NaN        NaN        NaN        NaN        NaN   
1684        NaN        NaN        NaN        NaN        NaN        NaN   

                            
time 351.000000 355.200000  
0           NaN        NaN  
1           NaN        NaN  
2           NaN        NaN  
3           NaN        NaN  
4           NaN        NaN  
...         ...        ...  
1680        NaN        NaN  
1681        NaN        NaN  
1682        NaN        NaN  
1683   0.071242        NaN  
1684        NaN   0.026208  

[1685 rows x 3206555 columns]

In [ ]:
df_survival

time  patient_0  patient_1  patient_2  patient_3  patient_4  \
0       0.100000   0.999411   0.999524   0.999449   0.999417   0.999563   
1       0.766667   0.999411   0.999524   0.999449   0.999417   0.999563   
2       1.233333   0.999411   0.999524   0.999449   0.999417   0.999563   
3       1.266667   0.999411   0.999524   0.999449   0.999417   0.999563   
4       1.433333   0.999411   0.999524   0.999449   0.999417   0.999563   
...          ...        ...        ...        ...        ...        ...   
1680  335.600000   0.071382   0.118476   0.084590   0.073326   0.141452   
1681  335.733340   0.052148   0.091928   0.063057   0.053739   0.112094   
1682  337.033330   0.052148   0.091928   0.063057   0.053739   0.112094   
1683  351.000000   0.027257   0.054421   0.034363   0.028275   0.069314   
1684  355.200000   0.006970   0.018080   0.009593   0.007331   0.025236   

      patient_5  patient_6  patient_7  patient_8  ...  patient_1893  \
0      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
1      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
2      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
3      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
4      0.999369   0.999524   0.999365   0.999519  ...      0.999524   
...         ...        ...        ...        ...  ...           ...   
1680   0.059152   0.118476   0.058105   0.116011  ...      0.118476   
1681   0.042258   0.091928   0.041422   0.089790  ...      0.091928   
1682   0.042258   0.091928   0.041422   0.089790  ...      0.091928   
1683   0.021090   0.054421   0.020583   0.052882  ...      0.054421   
1684   0.004894   0.018080   0.004732   0.017379  ...      0.018080   

      patient_1894  patient_1895  patient_1896  patient_1897  patient_1898  \
0         0.999524      0.999509      0.999412      0.999532      0.999532   
1         0.999524      0.999509      0.999412      0.999532      0.999532   
2         0.999524      0.999509      0.999412      0.999532      0.999532   
3         0.999524      0.999509      0.999412      0.999532      0.999532   
4         0.999524      0.999509      0.999412      0.999532      0.999532   
...            ...           ...           ...           ...           ...   
1680      0.118476      0.110997      0.071763      0.122733      0.122733   
1681      0.091928      0.085460      0.052459      0.095632      0.095632   
1682      0.091928      0.085460      0.052459      0.095632      0.095632   
1683      0.054421      0.049788      0.027456      0.057107      0.057107   
1684      0.018080      0.015993      0.007040      0.019322      0.019322   

      patient_1899  patient_1900  patient_1901  patient_1902  
0         0.999508      0.999524      0.999524      0.999568  
1         0.999508      0.999524      0.999524      0.999568  
2         0.999508      0.999524      0.999524      0.999568  
3         0.999508      0.999524      0.999524      0.999568  
4         0.999508      0.999524      0.999524      0.999568  
...            ...           ...           ...           ...  
1680      0.110159      0.118476      0.118476      0.144324  
1681      0.084738      0.091928      0.091928      0.114644  
1682      0.084738      0.091928      0.091928      0.114644  
1683      0.049275      0.054421      0.054421      0.071242  
1684      0.015766      0.018080      0.018080      0.026208  

[1685 rows x 1904 columns]

In [ ]:
data, target = load_metabric(path="/Users/JUSC/Documents/xgbsurv/xgbsurv/datasets/data/", as_frame=True)
target.max()

355.2

In [ ]:
#!conda remove --yes --prefix {sys.prefix}  -c sebp scikit-survival

In [ ]:
import numpy as np

from sksurv.datasets import load_gbsg2

from sksurv.linear_model import CoxPHSurvivalAnalysis

from sksurv.metrics import integrated_brier_score

from sksurv.preprocessing import OneHotEncoder

In [ ]:
X, y = load_gbsg2()

X.loc[:, "tgrade"] = X.loc[:, "tgrade"].map(len).astype(int)

Xt = OneHotEncoder().fit_transform(X)

/var/folders/jr/dh6mkdzs31lc5pkqymtdbh180000gp/T/ipykernel_75675/4250402329.py:3: DeprecationWarning:

In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`

/Users/JUSC/miniconda3/envs/xgbsurv/lib/python3.10/site-packages/sksurv/column.py:142: FutureWarning:

iteritems is deprecated and will be removed in a future version. Use .items instead.



In [ ]:
est = CoxPHSurvivalAnalysis(ties="efron").fit(Xt, y)
survs = est.predict_survival_function(Xt)

times = np.arange(365, 1826)

preds = np.asarray([[fn(t) for t in times] for fn in survs])
score = integrated_brier_score(y, y, preds, times)

print(score)

0.1815853064627424


In [ ]:
preds.shape

(686, 1461)

In [ ]:
survs.shape

(686,)

In [ ]:
survs[0]

StepFunction(x=array([   8.,   15.,   16.,   17.,   18.,   29.,   42.,   46.,   57.,
         63.,   65.,   67.,   71.,   72.,   98.,  113.,  114.,  120.,
        148.,  160.,  168.,  169.,  171.,  173.,  175.,  177.,  180.,
        181.,  184.,  186.,  191.,  195.,  205.,  213.,  223.,  227.,
        229.,  233.,  238.,  241.,  242.,  247.,  249.,  251.,  272.,
        273.,  275.,  276.,  281.,  285.,  286.,  288.,  293.,  296.,
        305.,  307.,  308.,  310.,  316.,  319.,  322.,  329.,  336.,
        338.,  343.,  344.,  348.,  350.,  353.,  357.,  358.,  359.,
        360.,  368.,  369.,  370.,  371.,  372.,  374.,  375.,  377.,
        379.,  385.,  392.,  394.,  403.,  410.,  415.,  417.,  420.,
        424.,  426.,  429.,  432.,  436.,  438.,  446.,  448.,  449.,
        455.,  456.,  460.,  461.,  463.,  465.,  471.,  473.,  475.,
        476.,  481.,  486.,  488.,  490.,  491.,  495.,  498.,  500.,
        502.,  503.,  504.,  515.,  518.,  525.,  526.,  529.,  530.,
     

In [ ]:
import xgboost as xgb
from xgboost import XGBRegressor
from sklearn.base import BaseEstimator, RegressorMixin
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_val_score, train_test_split, GridSearchCV, RandomizedSearchCV
from sklearn.datasets import make_regression
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_selection import VarianceThreshold
from sklearn.preprocessing import StandardScaler
from sklearn.feature_selection import SelectPercentile, f_regression
from sklearn.metrics import make_scorer, mean_absolute_error
xgbr_pipe = Pipeline(steps=[
                     ('xgbr',XGBSurv(n_estimators=2000, objective="breslow_objective", #"reg:squarederror",#custom_se,#'breslow_objective',#custom_se,
                                             eval_metric="breslow_loss",
                                             learning_rate=0.0001,
                                             random_state=7)) ])

learning_rate = [0.0001, 0.001, 0.01, 0.05, 0.1, 0.2, 0.3]
param_grid = dict(xgbr__learning_rate=learning_rate)

grid_search = RandomizedSearchCV(xgbr_pipe, param_grid, scoring="neg_mean_absolute_error", n_jobs=-1, cv=10)


In [ ]:
es = xgb.callback.EarlyStopping(
    rounds=10,
    #abs_tol=1e-3,
    save_best=True,
    maximize=False,
    #data_name="custom_validation_0",
    #metric_name="custom_validation",
)
# disable_default_eval_metric = True neecessary, otherwise rmse printed!!!
par = {'disable_default_eval_metric':1}
xgbr_pipe = Pipeline(steps=[
                     ('xgbr',XGBSurv(n_estimators=2000,
                                             objective="breslow_objective", #"reg:squarederror",#custom_se,#'breslow_objective',#custom_se,
                                             eval_metric="breslow_loss",
                                             learning_rate=0.0001,
                                             #callbacks=[es],
                                             random_state=7, early_stopping_rounds=75))    ])
# disable_default_eval_metric=True
learning_rate = [0.0001, 0.001, 0.01, 0.05, 0.1, 0.2, 0.3]
param_grid = dict(xgbr__learning_rate=learning_rate)

grid_search = RandomizedSearchCV(xgbr_pipe, param_grid, scoring="neg_mean_absolute_error", n_jobs=-1, cv=10)

grid_result = grid_search.fit(data, target, 
                    xgbr__eval_test_size=200
                    #xgbr__eval_metric='mae', 
                    )

/Users/JUSC/miniconda3/envs/xgbsurv/lib/python3.10/site-packages/sklearn/model_selection/_search.py:305: UserWarning:

The total space of parameters 7 is smaller than n_iter=10. Running 7 iterations. For exhaustive searches, use GridSearchCV.



1513
-5957.039104577258
200
-488.17474862718365
[0]	validation_0-rmse:126.73132	validation_0-breslow_likelihood:6.32382	validation_1-rmse:125.76062	validation_1-breslow_likelihood:4.28224
1513
-5957.003481289894
200
-488.17406021949625
[1]	validation_0-rmse:126.73130	validation_0-breslow_likelihood:6.32378	validation_1-rmse:125.76061	validation_1-breslow_likelihood:4.28223
1512
-5303.842800891509
200
-452.0768079138815
[0]	validation_0-rmse:154.18830	validation_0-breslow_likelihood:6.33673	validation_1-rmse:155.76525	validation_1-breslow_likelihood:4.26488
1513
-5660.927377193126
1513
-5956.9678649164525
200
-488.17337200031346
[2]	validation_0-rmse:126.73127	validation_0-breslow_likelihood:6.32374	validation_1-rmse:125.76060	validation_1-breslow_likelihood:4.28222
200
-481.40814549824836
[0]	validation_0-rmse:145.94387	validation_0-breslow_likelihood:6.31800	validation_1-rmse:144.29931	validation_1-breslow_likelihood:4.26025
1513
-5956.932257844803
200
-488.17268374742565
[3]	validati

## Fit Model

In [10]:
np.random.rand(20, 14)

array([[0.02181432, 0.03482534, 0.77356438, 0.98061598, 0.71188104,
        0.18826089, 0.80781902, 0.72112281, 0.95067566, 0.22622504,
        0.80247777, 0.68535704, 0.92776214, 0.8518429 ],
       [0.62611188, 0.50539977, 0.49677059, 0.85334536, 0.66563943,
        0.43885031, 0.76172526, 0.15330049, 0.52311621, 0.16626843,
        0.01558726, 0.50931536, 0.79785557, 0.75225774],
       [0.35884798, 0.84463118, 0.23483338, 0.33049988, 0.70028115,
        0.87490343, 0.0293598 , 0.96351021, 0.88309363, 0.61810293,
        0.03210043, 0.47510341, 0.76861197, 0.59432996],
       [0.69295342, 0.66341708, 0.58656637, 0.13077441, 0.84069016,
        0.03391392, 0.72025486, 0.41959227, 0.45038407, 0.65428101,
        0.8646159 , 0.82604988, 0.84538782, 0.97340962],
       [0.10210876, 0.76801964, 0.15020917, 0.01657109, 0.29992004,
        0.25849844, 0.14285787, 0.19400516, 0.59924029, 0.61853806,
        0.66347254, 0.82450758, 0.23622075, 0.56382214],
       [0.52857218, 0.44736546, 0.8